# Определение стоимости автомобилей

Сервис по продаже автомобилей с пробегом «Не бит, не крашен» разрабатывает приложение для привлечения новых клиентов. В нём можно быстро узнать рыночную стоимость своего автомобиля. В вашем распоряжении исторические данные: технические характеристики, комплектации и цены автомобилей. Вам нужно построить модель для определения стоимости. 

Заказчику важны:

- качество предсказания;
- скорость предсказания;
- время обучения.

## Подготовка данных

In [1]:
#!pip install ydata_profiling

In [2]:
#установим нужные библиотеки
#!pip install pandas-profiling

In [3]:
#!pip install catboost

In [4]:
#!pip install lightgbm

In [5]:
import pandas as pd
from ydata_profiling import ProfileReport
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.preprocessing import OrdinalEncoder, StandardScaler

from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV


from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostRegressor
from lightgbm import LGBMRegressor


random_state = 12345

import time
import warnings
warnings.filterwarnings('ignore')

In [6]:
#функция для отрисовки графика с усами и гистограммы
def describe_plot(data):
    position = 0
    plt.figure(figsize=[15, 20])
    plt.subplots_adjust(top=0.94, wspace=0.5, hspace=0.5)
    plt.suptitle('Распределение признаков.', fontsize=15)

    for column_name in data.columns:
        position += 1
        plt.subplot(5, 2, position)
        sns.set_style('darkgrid')
        plt.title(f'Ящик с усами для параметра {column_name.upper()}', fontsize=10)
        sns.set_style('darkgrid')
        sns.boxplot(data=data[column_name], orient='h')
        plt.axvline(np.mean(data[column_name]), 
                color='r', 
                linestyle='-',
                label='Среднее')
        plt.legend(title=f'Среднее = {np.mean(data[column_name]):.2f}, Медиана = {np.median(data[column_name]):.2f}', 
               loc='center', 
               edgecolor = 'r',
               facecolor = 'oldlace',
               bbox_to_anchor=(0.5, -0.24))
        position += 1
        plt.subplot(5, 2, position)
        sns.set_style('darkgrid')
        plt.title(f'Гистограмма для параметра {column_name.upper()}', fontsize=10)
        sns.histplot(data[column_name], color='b', kde=False)
    plt.show();

In [7]:
try:
    df = pd.read_csv('/datasets/autos.csv')
    
except:
    df = pd.read_csv('https://code.s3.yandex.net/datasets/autos.csv')

In [8]:
# Создадим копию, чтобы не менять данные в исходном датафрейме
data = df.copy()

### Изучение данных

In [9]:
data.head()

DateCrawled  Price VehicleType  RegistrationYear Gearbox  Power  \
0  2016-03-24 11:52:17    480         NaN              1993  manual      0   
1  2016-03-24 10:58:45  18300       coupe              2011  manual    190   
2  2016-03-14 12:52:21   9800         suv              2004    auto    163   
3  2016-03-17 16:54:04   1500       small              2001  manual     75   
4  2016-03-31 17:25:20   3600       small              2008  manual     69   

   Model  Kilometer  RegistrationMonth  FuelType       Brand Repaired  \
0   golf     150000                  0    petrol  volkswagen      NaN   
1    NaN     125000                  5  gasoline        audi      yes   
2  grand     125000                  8  gasoline        jeep      NaN   
3   golf     150000                  6    petrol  volkswagen       no   
4  fabia      90000                  7  gasoline       skoda       no   

           DateCreated  NumberOfPictures  PostalCode             LastSeen  
0  2016-03-24 00:00:00                 0       70435  2016-04-07 03:16:57  
1  2016-03-24 00:00:00                 0       66954  2016-04-07 01:46:50  
2  2016-03-14 00:00:00                 0       90480  2016-04-05 12:47:46  
3  2016-03-17 00:00:00                 0       91074  2016-03-17 17:40:17  
4  2016-03-31 00:00:00                 0       60437  2016-04-06 10:17:21

In [10]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 354369 entries, 0 to 354368
Data columns (total 16 columns):
 #   Column             Non-Null Count   Dtype 
---  ------             --------------   ----- 
 0   DateCrawled        354369 non-null  object
 1   Price              354369 non-null  int64 
 2   VehicleType        316879 non-null  object
 3   RegistrationYear   354369 non-null  int64 
 4   Gearbox            334536 non-null  object
 5   Power              354369 non-null  int64 
 6   Model              334664 non-null  object
 7   Kilometer          354369 non-null  int64 
 8   RegistrationMonth  354369 non-null  int64 
 9   FuelType           321474 non-null  object
 10  Brand              354369 non-null  object
 11  Repaired           283215 non-null  object
 12  DateCreated        354369 non-null  object
 13  NumberOfPictures   354369 non-null  int64 
 14  PostalCode         354369 non-null  int64 
 15  LastSeen           354369 non-null  object
dtypes: int64(7), object(

Описание данных

Признаки
* DateCrawled — дата скачивания анкеты из базы
* VehicleType — тип автомобильного кузова
* RegistrationYear — год регистрации автомобиля
* Gearbox — тип коробки передач
* Power — мощность (л. с.)
* Model — модель автомобиля
* Kilometer — пробег (км)
* RegistrationMonth — месяц регистрации автомобиля
* FuelType — тип топлива
* Brand — марка автомобиля
* Repaired — была машина в ремонте или нет
* DateCreated — дата создания анкеты
* NumberOfPictures — количество фотографий автомобиля
* PostalCode — почтовый индекс владельца анкеты (пользователя)
* LastSeen — дата последней активности пользователя

Целевой признак
* Price — цена (евро)

In [11]:
#Приведем названия переменных к нижнему регистру.
data.columns = data.columns.str.lower().str.replace(' ', '_')

In [12]:
#Приведём названия переменных к змеиному виду
data = data.rename(columns={'datecrawled':'date_crawled', 
                        'vehicletype':'vehicle_type', 
                        'registrationyear':'registration_year', 
                        'registrationmonth':'registration_month', 
                        'fueltype':'fuel_type', 
                        'notrepaired':'not_repaired', 
                        'datecreated':'date_created',
                        'numberofpictures': 'number_of_pictures',
                        'postalcode':'postal_code',
                        'lastseen':'date_last_seen'})

In [13]:
# Для удобства, поменяем столбцы местами
data = data[['date_created', 'date_crawled','date_last_seen', 'price', 'postal_code',
         'registration_year',  'registration_month', 'brand', 'model', 'kilometer', 'repaired',
         'vehicle_type',  'gearbox', 'power',   'fuel_type', 
         'number_of_pictures']]

In [14]:
#проверим
data.columns

Index(['date_created', 'date_crawled', 'date_last_seen', 'price',
       'postal_code', 'registration_year', 'registration_month', 'brand',
       'model', 'kilometer', 'repaired', 'vehicle_type', 'gearbox', 'power',
       'fuel_type', 'number_of_pictures'],
      dtype='object')

Воспользуемся вспомогательным инструментом, для анализа полученных данных.

In [15]:
ProfileReport(data)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Выводы:
1. В данных всего 4 явных дубликата.
2. В данных есть пропуски, в дальнейшем необходиом их обработать.

по каждому признаку:

* `date_created (дата создания анкеты)`: большая часть объявлений размещены в марте-апреле 2016 года. Думаю, что данный параметр не стоит рассматривать при моделировании цены автомобиля.


* `date_crawled (дата скачивания анкеты из базы)`: данные всего за два месяца (март-апрель 2016 года). Думаю, что данный параметр не стоит рассматривать при моделировании цены автомобиля.


* `date_last_seen (дата последней активности пользователя)`: данные всего за два месяца (март-апрель 2016 года). Думаю, что данный параметр не стоит рассматривать при моделировании цены автомобиля.


* `price (цена (евро))`: ,большое кол-во "бесплатных" автомобилей, от этих данных необходимо будет избавиться.


* `postal_code` — почтовый индекс владельца анкеты (пользователя)


* `registration_year` (год регистрации автомобиля): в данных существуют аномальные значения, необходимо будет от них избавиться.


* `registration_month (месяц регистрации автомобиля)`: есть нулевой месяц.


* `brand (марка автомобиля)`: есть пропуски, которые необходимо будет обработать. Самый популярный брэнд - "volkswagen".


* `model (модель автомобиля)`: есть пропуски, которые необходимо будет обработать. Самая популярная модель - "golf".


* `kilometer (пробег (км))`: максимальное значение 150 тысяч км., видимо на сайте ввод ограничен данным значением.


* `repaired (была машина в ремонте или нет)`: есть пропуски, которые необходимо будет обработать.


* `vehicle_type (тип автомобильного кузова)`: есть пропуски, которые необходимо будет обработать. Самый популярный тип кузова - "sedan".


* `gearbox (тип коробки передач)`: есть пропуски, которые необходимо будет обработать. Больше всего автомобилей с ручной коробкой передач.


* `power (мощность (л. с.))`: есть нулевые значения мощности, а также аномально большие. В дальнейшем необходимо проанализировать.


* `fuel_type (тип топлива)`: есть пропуски, которые необходимо будет обработать. Больше всего автомобилей на бензине.



* `number_of_pictures (количество фотографий автомобиля)`: только нулевые значения. Не информативное поле. 

### Предобработка данных

In [16]:
data = data.drop_duplicates()

In [17]:
#pd.to_datetime(data['date_created']).dt.to_period('M')
data['date_created'] = pd.to_datetime(data['date_created']).dt.to_period('M')
data['date_crawled'] = pd.to_datetime(data['date_crawled']).dt.to_period('M')
data['date_last_seen'] = pd.to_datetime(data['date_last_seen']).dt.to_period('M')

In [18]:
plt.figure(figsize=(15, 8))
sns.heatmap(data.isna().transpose())

<Axes: >

In [19]:
data.isna().sum()

date_created              0
date_crawled              0
date_last_seen            0
price                     0
postal_code               0
registration_year         0
registration_month        0
brand                     0
model                 19705
kilometer                 0
repaired              71154
vehicle_type          37490
gearbox               19833
power                     0
fuel_type             32895
number_of_pictures        0
dtype: int64

In [20]:
#Заполним пропуски в категориальных признаках.
data['model'] = data['model'].fillna('unknown')
data['repaired'] = data['repaired'].fillna('unknown')
data['vehicle_type'] = data['vehicle_type'].fillna('unknown')
data['gearbox'] = data['gearbox'].fillna('unknown')
data['fuel_type'] = data['fuel_type'].fillna('unknown')

In [21]:
data.isna().sum()

date_created          0
date_crawled          0
date_last_seen        0
price                 0
postal_code           0
registration_year     0
registration_month    0
brand                 0
model                 0
kilometer             0
repaired              0
vehicle_type          0
gearbox               0
power                 0
fuel_type             0
number_of_pictures    0
dtype: int64

In [22]:
#Избавимся от строк с нулевой ценой
data = data[data['price']!=0]

Избавимся от машин с аномальнам годом регистрации.

In [23]:
plt.figure(figsize=(15, 8))
plt.xlim(1960,2016)
sns.histplot(data=data['registration_year']);

In [24]:
data = data.query('registration_year>=1980 and registration_year<=2016')

In [25]:
print(df.shape, data.shape)

(354369, 16) (326648, 16)


Избавимся от машин с аномальными значениями мощности.

In [26]:
plt.figure(figsize=(15, 8))
plt.xlim(10,500)
sns.histplot(data=data['power']);

In [27]:
data = data.query('power<=500')

Заполним пропуски в параметре `power` медианным значением в разрезе бренда и модели.

In [28]:
car_power = data.query('power>0').groupby(['brand','model']).agg({'power':['median']}).reset_index()

In [29]:
car_power.columns = ['car_brand', 'car_model', 'car_power']

In [30]:
car_power

car_brand car_model  car_power
0    alfa_romeo       145      103.0
1    alfa_romeo       147      120.0
2    alfa_romeo       156      150.0
3    alfa_romeo       159      170.0
4    alfa_romeo     other      150.0
..          ...       ...        ...
330       volvo       v40      116.0
331       volvo       v50      136.0
332       volvo       v60      163.0
333       volvo       v70      163.0
334       volvo  xc_reihe      185.0

[335 rows x 3 columns]

In [31]:
data = data.merge(car_power, left_on=['brand','model'], right_on=['car_brand','car_model'])

In [32]:
#
def go_power(row):
    if row['power'] == 0:
        return row['car_power']
    else:
        return row['power']

data['power'] = data.apply(go_power, axis=1)

In [33]:
data

date_created date_crawled date_last_seen  price  postal_code  \
0           2016-03      2016-03        2016-04    480        70435   
1           2016-03      2016-03        2016-03   1500        91074   
2           2016-03      2016-03        2016-03    999        27472   
3           2016-03      2016-03        2016-03    245        44145   
4           2016-03      2016-03        2016-03    350        19386   
...             ...          ...            ...    ...          ...   
326257      2016-03      2016-03        2016-04   2950         4451   
326258      2016-03      2016-03        2016-04   1500        25524   
326259      2016-03      2016-03        2016-03   2800        17279   
326260      2016-03      2016-03        2016-04   1950        83278   
326261      2016-03      2016-03        2016-04    550        88518   

        registration_year  registration_month       brand       model  \
0                    1993                   0  volkswagen        golf   
1                    2001                   6  volkswagen        golf   
2                    1998                   0  volkswagen        golf   
3                    1994                   2  volkswagen        golf   
4                    2016                   4  volkswagen        golf   
...                   ...                 ...         ...         ...   
326257               1999                   9      lancia       kappa   
326258               1998                   4      lancia       kappa   
326259               1999                  10       rover  freelander   
326260               2000                   1       rover  freelander   
326261               1997                   7       rover    defender   

        kilometer repaired vehicle_type  gearbox  power fuel_type  \
0          150000  unknown      unknown   manual  101.0    petrol   
1          150000       no        small   manual   75.0    petrol   
2          150000  unknown        small   manual  101.0   unknown   
3          150000       no        sedan  unknown  101.0    petrol   
4          150000       no      unknown   manual   75.0    petrol   
...           ...      ...          ...      ...    ...       ...   
326257     150000       no        wagon   manual  155.0       lpg   
326258     125000       no        sedan   manual  150.0    petrol   
326259     150000  unknown          suv   manual  177.0  gasoline   
326260     150000       no          suv     auto  177.0    petrol   
326261     150000       no        small   manual   75.0    petrol   

        number_of_pictures   car_brand   car_model  car_power  
0                        0  volkswagen        golf      101.0  
1                        0  volkswagen        golf      101.0  
2                        0  volkswagen        golf      101.0  
3                        0  volkswagen        golf      101.0  
4                        0  volkswagen        golf      101.0  
...                    ...         ...         ...        ...  
326257                   0      lancia       kappa      155.0  
326258                   0      lancia       kappa      155.0  
326259                   0       rover  freelander      177.0  
326260                   0       rover  freelander      177.0  
326261                   0       rover    defender       75.0  

[326262 rows x 19 columns]

In [34]:
describe_plot(data[['price', 'power', 'kilometer']])

In [35]:
drop_columns = ['date_last_seen', 'date_crawled', 'date_created', 'number_of_pictures', 
                'car_brand','car_model','car_power', 'postal_code', 'registration_month']
data = data.drop(columns=drop_columns)

Посмотрим, сколько данных мы потеряли, после предобработки.

In [36]:
print('Размер изначальной выборки:',df.shape)
print('Размер обработанной выборки:',data.shape)
print(f'Удалено {100*(1-data.shape[0]/df.shape[0])}%')


Размер изначальной выборки: (354369, 16)
Размер обработанной выборки: (326262, 10)
Удалено 7.93156286244%


Удалено менее 10% данных. Можем переходить к обучению моделей.

## Обучение моделей

In [37]:
data_oe = data

Выделим целевую переменную и разделим выборку на обучающую и тестовую.

In [38]:
target_oe = data_oe['price']
features_oe = data_oe.drop('price', axis=1)

features_train_oe, features_test_oe, target_train_oe, target_test_oe = \
train_test_split(features_oe, target_oe, test_size=0.3, random_state=random_state) 

print(features_train_oe.shape)
print(features_test_oe.shape)

(228383, 9)
(97879, 9)


In [39]:
# закодируем признаки с помощью порядкового кодирования

category = ['registration_year', 'brand', 'model', 'kilometer', 'repaired', 'vehicle_type', 'gearbox', 'power', 'fuel_type']
encoder = OrdinalEncoder(handle_unknown='use_encoded_value', unknown_value=9999)
encoder.fit(features_train_oe[category])
features_train_oe[category] = encoder.transform(features_train_oe[category])
features_test_oe[category] = encoder.transform(features_test_oe[category])

Проведём масштабирование признаков.

In [40]:
numeric = list(features_oe)
scaler_oe = StandardScaler()
scaler_oe.fit(features_train_oe[numeric])

StandardScaler()

In [41]:
features_train_oe[numeric] = scaler_oe.transform(features_train_oe[numeric])
features_test_oe[numeric] = scaler_oe.transform(features_test_oe[numeric])

In [42]:
features_train_oe.head()

registration_year     brand     model  kilometer  repaired  \
19215            0.511715  1.293004  0.030619  -2.913572 -0.576961   
116749           0.013759  0.015668  0.700883   0.500345 -0.576961   
169115           0.345730 -1.487079 -1.159443   0.500345 -0.576961   
111316           0.345730 -0.059469 -0.256637   0.500345 -0.576961   
213849          -1.148138  0.691905  0.085334   0.500345  2.451597   

        vehicle_type   gearbox     power  fuel_type  
19215      -0.266572  0.311235  1.529362   0.600667  
116749      0.150478  0.311235 -0.034910   0.600667  
169115      1.401630 -1.839275  0.864097  -1.517084  
111316     -0.266572 -1.839275  0.630355  -1.517084  
213849      0.150478  0.311235 -1.185638   0.600667

Мы закодировали категориальные признаки, выделили целевую переменную, разделили выборку на обучающую и тренировочную и масштабировали признаки. Переходим к обучению моделей.

### Случайный лес (Random Forest)

Найдём оптимальные гиперпараметры для модели Random Forest.

In [43]:
%%time

model_rf_oe = RandomForestRegressor(random_state=random_state)
parametrs = {'n_estimators': range(10,151,10),
              'max_depth': range(2, 11)}

search_rf = GridSearchCV(model_rf_oe, parametrs, cv=3, scoring='neg_root_mean_squared_error', n_jobs=-1)
search_rf.fit(features_train_oe, target_train_oe)

CPU times: total: 54.4 s
Wall time: 27min 42s


GridSearchCV(cv=3, estimator=RandomForestRegressor(random_state=12345),
             n_jobs=-1,
             param_grid={'max_depth': range(2, 11),
                         'n_estimators': range(10, 151, 10)},
             scoring='neg_root_mean_squared_error')

In [44]:
print(search_rf.best_params_)

{'max_depth': 10, 'n_estimators': 150}


In [45]:
print(search_rf.best_score_*-1)

1852.8905283619117


### LightGBM

Найдём оптимальные гиперпараметры для модели LightGBM.

In [46]:
%%time

model_lgb_oe = LGBMRegressor(random_state=random_state)
parametrs = {'n_estimators': [10, 100, 1000],'max_depth': range(2, 11)}

search_lgb_oe = GridSearchCV(model_lgb_oe, parametrs, cv=3, scoring='neg_root_mean_squared_error', n_jobs=-1)
search_lgb_oe.fit(features_train_oe, target_train_oe)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005121 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 613
[LightGBM] [Info] Number of data points in the train set: 228383, number of used features: 9
[LightGBM] [Info] Start training from score 4580.032117
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
CPU times: total: 14 s
Wall time: 1min 46s


GridSearchCV(cv=3, estimator=LGBMRegressor(random_state=12345), n_jobs=-1,
             param_grid={'max_depth': range(2, 11),
                         'n_estimators': [10, 100, 1000]},
             scoring='neg_root_mean_squared_error')

In [47]:
print(search_lgb_oe.best_params_)

{'max_depth': 10, 'n_estimators': 1000}


In [48]:
print(search_lgb_oe.best_score_*-1)

1545.20011528062


### CatBoost

Найдём оптимальные гиперпараметры для модели CatBoost

In [49]:
%%time

model_cbr_oe = CatBoostRegressor(random_state=random_state)
parametrs = {'n_estimators': [10, 100, 1000],'max_depth': range(2, 11)}

search_cbr_oe = GridSearchCV(model_cbr_oe, parametrs, cv=3, scoring='neg_root_mean_squared_error', n_jobs=-1)
search_cbr_oe.fit(features_train_oe, target_train_oe)

Learning rate set to 0.096571
0:	learn: 4212.0008512	total: 98.3ms	remaining: 1m 38s
1:	learn: 3930.3270021	total: 145ms	remaining: 1m 12s
2:	learn: 3684.3022346	total: 197ms	remaining: 1m 5s
3:	learn: 3467.1964151	total: 247ms	remaining: 1m 1s
4:	learn: 3275.1733866	total: 296ms	remaining: 58.9s
5:	learn: 3103.3286959	total: 339ms	remaining: 56.2s
6:	learn: 2952.7848208	total: 389ms	remaining: 55.2s
7:	learn: 2820.8249124	total: 441ms	remaining: 54.7s
8:	learn: 2700.5042181	total: 494ms	remaining: 54.4s
9:	learn: 2596.7553018	total: 536ms	remaining: 53s
10:	learn: 2506.3482902	total: 580ms	remaining: 52.2s
11:	learn: 2429.3295680	total: 624ms	remaining: 51.4s
12:	learn: 2357.9788566	total: 675ms	remaining: 51.2s
13:	learn: 2296.9780724	total: 717ms	remaining: 50.5s
14:	learn: 2243.9267077	total: 773ms	remaining: 50.7s
15:	learn: 2195.9943431	total: 834ms	remaining: 51.3s
16:	learn: 2155.0578048	total: 888ms	remaining: 51.3s
17:	learn: 2118.8648372	total: 945ms	remaining: 51.6s
18:	lea

GridSearchCV(cv=3,
             estimator=<catboost.core.CatBoostRegressor object at 0x000001E901731940>,
             n_jobs=-1,
             param_grid={'max_depth': range(2, 11),
                         'n_estimators': [10, 100, 1000]},
             scoring='neg_root_mean_squared_error')

In [50]:
print(search_cbr_oe.best_params_)
print(search_cbr_oe.best_score_*-1)

{'max_depth': 10, 'n_estimators': 1000}
1536.4689427281648


Мы подобрали оптимальные гиперпараметры для трёх моделей. Далее проанализируем их.

## Анализ моделей

Сравним наши модели с подобранными гиперпараметрами.

In [51]:
print(search_rf.best_params_)
print(search_lgb_oe.best_params_)
print(search_cbr_oe.best_params_)

{'max_depth': 10, 'n_estimators': 150}
{'max_depth': 10, 'n_estimators': 1000}
{'max_depth': 10, 'n_estimators': 1000}


In [52]:
models = [['RandomForestRegressor',RandomForestRegressor(max_depth=10, n_estimators=150, random_state=random_state)],\
          ['LGBMRegressor', LGBMRegressor(max_depth=10, n_estimators=1000, random_state=random_state)],\
          ['CatBoostRegressor', CatBoostRegressor(max_depth=10, n_estimators=1000, random_state=random_state,verbose=False)]]

In [53]:
def learn_models(models, x_train, y_train, model='default', regr_name='', n_jobs=-1):
    # Инициализируем пустой DataFrame
    results = pd.DataFrame(columns=['Regressor', 'Train RMSE score', 'Learning Time', 'Prediction Time'])
    
    for model_info in models:
        start_learning = time.time()
        model_info[1].fit(x_train, y_train)
        end_learning = time.time()
        duration_learning = end_learning - start_learning
        
        start_prediction = time.time()
        prediction = model_info[1].predict(x_train)
        end_prediction = time.time()
        duration_prediction = end_prediction - start_prediction
        train_rmse_score = mean_squared_error(y_train, prediction, squared=False)
        
        if regr_name == '':
            name = model_info[0]
        else:
            name = regr_name
        
        # Создаем временный DataFrame для текущих результатов
        temp_df = pd.DataFrame({
            'Regressor': [name],
            'Train RMSE score': [round(train_rmse_score, 2)],
            'Learning Time': [round(duration_learning, 2)],
            'Prediction Time': [round(duration_prediction, 2)]
        })
        
        # Используем pd.concat для объединения временного DataFrame с основным
        results = pd.concat([results, temp_df], ignore_index=True)
    return results

In [54]:
learn_models(models,features_train_oe, target_train_oe)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.008481 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 613
[LightGBM] [Info] Number of data points in the train set: 228383, number of used features: 9
[LightGBM] [Info] Start training from score 4580.032117
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).


Regressor  Train RMSE score  Learning Time  Prediction Time
0  RandomForestRegressor           1785.12          50.92             3.00
1          LGBMRegressor           1384.44           3.45             2.81
2      CatBoostRegressor           1320.93          45.39             0.55

Вывод:


* Быстрее всех обучается модель LGBMRegressor, но предсказывает быстрее всех модель CatBoostRegressor, и при этом показывают наибольшую точность.
* Исходя из полученных результатов, мы порекомендуем заказчику модель CatBoostRegressor.

## Тестирование лучшей модели

In [55]:
model_cbr_oe = CatBoostRegressor(max_depth=10, n_estimators=1000, random_state=random_state,verbose=False)
model_cbr_oe.fit(features_train_oe, target_train_oe)

predictions_train_cbr_oe = model_cbr_oe.predict(features_train_oe)
rmse_cbr_oe_train = mean_squared_error(target_train_oe, predictions_train_cbr_oe)**0.5
r2_cbr_oe_train = r2_score(target_train_oe, predictions_train_cbr_oe)

predictions_test_cbr_oe = model_cbr_oe.predict(features_test_oe)
rmse_cbr_oe_test = mean_squared_error(target_test_oe, predictions_test_cbr_oe)**0.5
r2_cbr_oe_test = r2_score(target_test_oe, predictions_test_cbr_oe)

print('RMSE на обучающей выборке:', rmse_cbr_oe_train)
print('R2 на обучающей выборке:', r2_cbr_oe_train)
print('RMSE на тестовой выборке:', rmse_cbr_oe_test)
print('R2 на тестовой выборке:', r2_cbr_oe_test)

RMSE на обучающей выборке: 1320.9309567196171
R2 на обучающей выборке: 0.9148272226236774
RMSE на тестовой выборке: 1514.3188395005177
R2 на тестовой выборке: 0.8879951449354088


Выведем информацию по важности признаков, полученной модели.

In [56]:
feature_imp = pd.Series(model_cbr_oe.feature_importances_,index=features_train_oe.columns).sort_values(ascending=False)

In [59]:
plt.figure(figsize=(15, 8))
sns.barplot(x=feature_imp, y=feature_imp.index)
plt.xlabel('Важность признаков')
plt.ylabel('Признаки')
plt.title('Визуализация важных признаков')
plt.show()

Наибольший вклад в предсказание целевого признака вносит год регистрации автомобиля.

## Итоговый вывод

* Мы провели исследование полученных данных, избавились от аномалий.


* Обучили 3 модели (Random Forest, LightGBM, Catboost) для прогнозирования стоимости автомобиля.


* Проанализировали полученные модели и обнаружили, что быстрее всех обучается модель LGBMRegressor, но предсказывает быстрее всех модель CatBoostRegressor, и при этом показывает наибольшую точность.


* Исходя из требований заказчика по скорости обучения и по качеству модели, мы порекомендуем заказчику модель CatBoostRegressor.